# Remplis ta ville

In [1]:
import ipywidgets as widgets
from IPython import display
import os

Trouves-tu que ta région n'est pas assez encombrée par le trafic de transit, qu'elle n'est pas assez bruyante, que l'air et les eaux n'y sont pas assez pollués ? Eh bien, tu te trouves sur la bonne page ! Choisis ta région parmi la liste et laisse-moi te montrer ce que représente la quantité de trafic automobile supplémentaire estimée par l'Office Fédéral des Routes (OFROU) engendrée par l'extension de la largeur des autoroutes.

In [2]:
places = {
    "geneva": {"shorthand": "geneva", "friendly": "Ville de Genève", "label": "Geneva, Switzerland", "cars": 44_000, "node": 2809410},
    "coppet": {"shorthand": "coppet", "friendly": "Région de Coppet", "label": ["Commugny, Switzerland","Coppet, Switzerland","Founex, Switzerland"], "cars": 8_800, "node": 6514705484},
    "nyon":   {"shorthand": "nyon",   "friendly": "Ville de Nyon", "label": "Nyon, Switzerland",   "cars": 7_000, "node": 311240719},
}

mots = {
    "car":  {"shorthand": "car",  "friendly": "Voiture", "ppv": 1.5, "length": 7},
    "bus":  {"shorthand": "bus",  "friendly": "Bus", "ppv": 132, "length": 21},
    "bike": {"shorthand": "bike", "friendly": "Vélo","ppv": 1,   "length": 0.5},
}

w_place = widgets.Dropdown(
    options=[(places[place]["friendly"],places[place]["shorthand"]) for place in places.keys()],
    description='Région',
)

w_mot = widgets.Dropdown(
    options=[(mots[mot]["friendly"],mots[mot]["shorthand"]) for mot in mots.keys()],
    description='Véhicule',
)

w_submit = widgets.Button(
    description='Remplir !',
    disabled=False
)

w_progress = widgets.IntProgress(
    min=0,
    description=' ',
    orientation='horizontal'
)

def simulate(*ignore):
    
    import geopandas as gpd
    import pandas as pd
    import networkx as nx
    import osmnx as ox
    import numpy as np
    
    place = places[w_place.value]
    mot = mots[w_mot.value]
    
    people = place["cars"] * mots["car"]["ppv"]
    
    vehicles = np.ceil(people / mot["ppv"])

    # Download regional roads graph and convert it to GeoDataFrame
    
    utw = ["name","highway","access","length","lanes","lanes:forward","lanes:backward","lanes:psv","lanes:psv:forward","lanes:psv:backward","lanes:bus","lanes:bus:forward","lanes:bus:backward","motor_vehicle"]
    ox.settings.useful_tags_way=utw

    w_progress.description = "Chargement du graphe"
    w_progress.value = 0
    G = ox.graph_from_place(place["label"], network_type="drive")
    
    # Estimate and clean:
    # 
    #  * Lanes dedicated to motorized individual transport
    #  * Lanes length
    #  * Lanes cars capacity

    w_progress.description = "Annotation du graphe"
    edges = ox.graph_to_gdfs(G, nodes=False, edges=True)

    w_progress.description = "Estimation des capacités"
    edges["lanes:forward"]  = edges["lanes:forward"].fillna(0) if "lanes:forward" in edges.columns else 0
    edges["lanes:forward"]  = edges.apply(lambda row: np.min(np.array(row["lanes:forward"]).astype(int)), axis=1)
    edges["lanes:backward"] = edges["lanes:backward"].fillna(0) if "lanes:backward" in edges.columns else 0
    edges["lanes:backward"] = edges.apply(lambda row: np.min(np.array(row["lanes:backward"]).astype(int)), axis=1)
    edges["lanes"]          = edges["lanes"].fillna(0) if "lanes" in edges.columns else 0
    edges["lanes"]          = edges.apply(lambda row: np.min(np.array(row["lanes"]).astype(int)), axis=1)

    edges["lanes:psv"]          = edges["lanes:psv"].fillna(0) if "lanes:psv" in edges.columns else 0
    edges["lanes:psv"]          = edges.apply(lambda row: np.min(np.array(row["lanes:psv"]).astype(int)), axis=1)
    edges["lanes:psv:forward"]  = edges["lanes:psv:forward"].fillna(0) if "lanes:psv:forward" in edges.columns else 0
    edges["lanes:psv:forward"]  = edges.apply(lambda row: np.min(np.array(row["lanes:psv:forward"]).astype(int)), axis=1)
    edges["lanes:psv:backward"] = edges["lanes:psv:backward"].fillna(0) if "lanes:psv:backward" in edges.columns else 0
    edges["lanes:psv:backward"] = edges.apply(lambda row: np.min(np.array(row["lanes:psv:backward"]).astype(int)), axis=1)

    edges["lanes:bus"]          = edges["lanes:bus"].fillna(0) if "lanes:bus" in edges.columns else 0
    edges["lanes:bus"]          = edges.apply(lambda row: np.min(np.array(row["lanes:bus"]).astype(int)), axis=1)
    edges["lanes:bus:forward"]  = edges["lanes:bus:forward"].fillna(0) if "lanes:bus:forward" in edges.columns else 0
    edges["lanes:bus:forward"]  = edges.apply(lambda row: np.min(np.array(row["lanes:bus:forward"]).astype(int)), axis=1)
    edges["lanes:bus:backward"] = edges["lanes:bus:backward"].fillna(0) if "lanes:bus:backward" in edges.columns else 0
    edges["lanes:bus:backward"] = edges.apply(lambda row: np.min(np.array(row["lanes:bus:backward"]).astype(int)), axis=1)

    edges["lanes:mit"] = edges.apply(lambda row: np.max([row["lanes"],row["lanes:forward"]+row["lanes:backward"],2]) - np.max([row["lanes:psv"],row["lanes:psv:forward"]+row["lanes:psv:backward"],row["lanes:bus:backward"]]), axis=1)

    edges["highway"]       = edges["highway"] if "highway" in edges.columns else ""
    edges["motor_vehicle"] = edges["motor_vehicle"] if "motor_vehicle" in edges.columns else ""
    edges["access"]        = edges["access"] if "access" in edges.columns else ""
    
    edges["lanes:mit"] = edges.apply(lambda row: (0 if np.isin(row["highway"],["residential","living_street"]).any() else row["lanes:mit"]), axis=1)
    edges["lanes:mit"] = edges.apply(lambda row: (0 if np.isin(row["motor_vehicle"],["no","private","destination","agricultural","forestry","delivery"]).any() else row["lanes:mit"]), axis=1)
    edges["lanes:mit"] = edges.apply(lambda row: (0 if np.isin(row["access"], ["no","destination"]).any() else row["lanes:mit"]), axis=1)

    edges["length"] = edges["length"].fillna(0)
    
    edges["capacity"] = edges.apply(lambda row: np.floor(row["length"] * row["lanes:mit"] / mot["length"]), axis=1)
    
    edges_reset = edges.copy()
    
    # print(f"Occupancy : {vehicles / sum(edges["capacity"])}")

    # Colorize the plotted roads graph:

    w_progress.description = "Remplissage des rues"
    
    counter = 0
    nodes = [place["node"]];
    shoteach = vehicles / 10;
    
    edges = edges_reset.copy()
    
    edges_copy = pd.DataFrame(index=edges.index)
    edges_copy["occupancy"] = 0
    edges_copy["capacity"] = edges["capacity"]
    lastshot = 0

    w_progress.max = vehicles
    
    while counter < vehicles and nodes:
        
        idx = nodes.pop(0)
        if idx in edges.index.get_level_values(0).values:
            nodedges = edges.loc[idx]
            nodedges_copy = edges_copy.loc[idx]
            for i,r in nodedges.iterrows():
                #print(nodes,counter,r["capacity"],nodedges_copy.loc[i,"occupancy"],edges.shape[0])
                if counter >= vehicles:
                    break
        
                if not nodedges_copy.loc[i,"occupancy"]:
                    nodedges_copy.loc[i,"occupancy"] = r["capacity"]
                    counter += r["capacity"]
                    w_progress.value = counter
                    nodes.append(i[0])
            edges.drop(idx, inplace=True)
            if counter // shoteach > lastshot:
                lastshot += 1
                
                edges_copy["color"] = edges_copy.apply(lambda row: 'darkred' if row["occupancy"] else 'darkseagreen', axis=1)
                edges_copy["color"] = edges_copy.apply(lambda row: 'darkgray' if not row["capacity"] else row["color"], axis=1)
                
                colors = edges_copy.loc[:,"color"].to_numpy()
                
                fig, ax = ox.plot_graph(G, edge_color=colors, node_size=15, edge_linewidth=5, filepath=f"./outputs/{place["shorthand"]}/plot_{mot["shorthand"]}_{lastshot}.svg", save=True, show=False, close=True)
        
    w_progress.description = "Terminé"

w_submit.on_click(simulate)

if os.environ.get('SERVER_SOFTWARE','jupyter').startswith('voila'):
    toolbar = widgets.HBox([widgets.VBox([w_place, w_mot])],layout=widgets.Layout(justify_content="center"))
else:
    toolbar = widgets.HBox([widgets.VBox([w_place, w_mot, w_submit, w_progress])],layout=widgets.Layout(justify_content="center"))

toolbar

Pour te donner une idée concrète de la quantité que cela représente, je vais les placer dans ta région. Imagine-toi ta région vide de voitures. Maintenant, remplis les routes de ta région une par une jusqu'à atteindre l'augmentation de la quantité de voitures prédite par l'OFROU en cas d'extension des autoroutes. Les routes complètement remplies sont représentées en rouge, celles encore vides en vert. Les routes représentées en gris sont des routes essentiellement résidentielles, elles ne sont donc pas prises en compte dans le calcul.

In [3]:
slider = widgets.IntSlider(min=1, max=10, step=1)

image = widgets.Image(format='svg+xml')

def compute(*ignore):
    file = open(f"./outputs/{places[w_place.value]["shorthand"]}/plot_{w_mot.value}_{slider.value}.svg", "rb")
    read = file.read()
    image.value = read

slider.observe(compute, 'value')

widgets.HBox([widgets.VBox([widgets.HBox([slider], layout=widgets.Layout(justify_content="center")), image], layout=widgets.Layout(max_width="700px"))], layout=widgets.Layout(justify_content="center"))

In [ ]:
from IPython.core.display import HTML
HTML("""
<style>
h1, p {
    display: block !important;
    max-width: 700px !important;
    margin: 0 auto !important;
}
</style>
""")